In [0]:
# Attached to: jira-json-cluster

# Your actual Python code goes here
# Make sure to write valid Python syntax in this section

In [0]:
%python
from pyspark.sql.functions import col

data_dir = "/Volumes/jira_story_point_estimator/default/jira_data_partitions"
partition_dirs = [f.path for f in dbutils.fs.ls(data_dir) if f.isDir()]

df = (
    spark.read
    .option("multiline", "true")
    .json([f"{d}/*.json" for d in partition_dirs])
    .repartition(5)
)

display(df)

In [0]:
df_transformed = (
    df.select(
        col("key"),
        col("fields.project.key").alias("project"),
        col("fields.created"),
        col("fields.resolutiondate"),
        col("fields.summary"),
        col("fields.description")
    )
    .dropna()
)

display(df_transformed)

In [0]:
df_transformed = (
    df.select(
        col("key"),
        col("fields.project.key").alias("project"),
        col("fields.created"),
        col("fields.resolutiondate"),
        col("fields.summary"),
        col("fields.description")
    )
    .dropna()
)

display(df_transformed)

In [0]:
row_count = df_transformed.count()
col_count = len(df_transformed.columns)
print(f"Rows: {row_count}, Columns: {col_count}")

In [0]:
from pyspark.sql.functions import col, regexp_replace

df_transformed_no_tz = df_transformed.withColumn(
    "created", regexp_replace(col("created"), r"\+\d$", "")
).withColumn(
    "resolutiondate", regexp_replace(col("resolutiondate"), r"\+\d$", "")
)

display(df_transformed_no_tz)

In [0]:
from pyspark.sql.functions import to_timestamp, col, unix_timestamp, regexp_replace

# Remove timezone information from the date fields
df_transformed_cleaned = df_transformed.withColumn(
    "created_cleaned", regexp_replace(col("created"), r"\+\d+$", "")
).withColumn(
    "resolutiondate_cleaned", regexp_replace(col("resolutiondate"), r"\+\d+$", "")
)

# Convert cleaned date fields to Unix timestamps
df_transformed_unix_timestamp = df_transformed_cleaned.withColumn(
    "created_unix", unix_timestamp(col("created_cleaned"), "yyyy-MM-dd'T'HH:mm:ss.SSS")
).withColumn(
    "resolutiondate_unix", unix_timestamp(col("resolutiondate_cleaned"), "yyyy-MM-dd'T'HH:mm:ss.SSS")
)

display(df_transformed_unix_timestamp)

In [0]:
from pyspark.sql.functions import col, expr

df_with_cycle_hours = (
    df_transformed_unix_timestamp
    .repartition(5)
    .withColumn(
        "cycle_hours",
        expr("ROUND((resolutiondate_unix - created_unix) / 3600, 0)")
    )
)

display(df_with_cycle_hours)

In [0]:
from pyspark.sql.functions import col, lit, array
from pyspark.ml.clustering import KMeans
from pyspark.ml.feature import VectorAssembler
from pyspark.sql.functions import udf
from pyspark.sql.types import ArrayType, DoubleType

# Assemble features for KMeans
assembler = VectorAssembler(
    inputCols=["cycle_hours"],
    outputCol="features"
)
df_features = assembler.transform(df_with_cycle_hours)

# Get distinct project list
projects = [
    row['project']
    for row in df_features.select("project").distinct().collect()
]

results = []
for project in projects:
    df_proj = df_features.filter(col("project") == project)
    if df_proj.count() >= 8:  # KMeans requires at least k rows
        kmeans = KMeans(
            k=8,
            seed=42,
            featuresCol="features"
        )
        model = kmeans.fit(df_proj)
        centroids = [float(c[0]) for c in model.clusterCenters()]
        df_proj = df_proj.withColumn("cycle_centroids", lit(centroids))
        results.append(df_proj)
    else:
        # Not enough data for clustering, fill with empty list
        df_proj = df_proj.withColumn("cycle_centroids", array())
        results.append(df_proj)

# Union all project DataFrames
from functools import reduce

df_with_centroids = reduce(
    lambda df1, df2: df1.unionByName(df2),
    results
)

# Use Python's built-in round, not pyspark.sql.functions.round
def round_centroids(centroids):
    return [float(round(float(c))) for c in centroids] if centroids else []

round_centroids_udf = udf(
    round_centroids,
    ArrayType(DoubleType())
)

df_with_centroids_rounded = df_with_centroids.withColumn(
    "cycle_centroids_rounded",
    round_centroids_udf(col("cycle_centroids"))
)

display(
    df_with_centroids_rounded.select(
        "project",
        "cycle_hours",
        "cycle_centroids_rounded"
    )
)

In [0]:
from pyspark.sql.functions import array_sort, map_from_arrays, array, lit

# Define the Fibonacci series as a Spark array
fibonacci = array([lit(x) for x in [1, 2, 3, 5, 8, 13, 21, 34]])
fib_length = 8

# Sort centroids for each row and pad/truncate to match Fibonacci length
df_with_sorted_centroids = df_with_centroids_rounded.withColumn(
    "sorted_centroids",
    array_sort(col("cycle_centroids_rounded"))
).withColumn(
    "centroids_padded",
    expr(
        f"""
        CASE 
            WHEN size(sorted_centroids) >= {fib_length} THEN slice(sorted_centroids, 1, {fib_length})
            ELSE concat(
                sorted_centroids, 
                array_repeat(sorted_centroids[array_max(transform(sequence(1, size(sorted_centroids)), x -> x))], {fib_length} - size(sorted_centroids))
            )
        END
        """
    )
).withColumn(
    "fib_to_centroid",
    map_from_arrays(fibonacci, col("centroids_padded"))
)

display(
    df_with_sorted_centroids.select(
        "project", "cycle_hours", "cycle_centroids_rounded", "fib_to_centroid"
    )
)

In [0]:
from pyspark import StorageLevel

df_with_sorted_centroids.persist(StorageLevel.MEMORY_AND_DISK)
df_with_sorted_centroids

In [0]:
display(df_with_sorted_centroids)

In [0]:
df_with_sorted_centroids.write.mode("overwrite").saveAsTable("df_with_sorted_centroids")

In [0]:
df_with_sorted_centroids.write.mode("overwrite").parquet("/mnt/backup/df_with_sorted_centroids_parquet")

In [0]:
df_with_sorted_centroids = spark.table("df_with_sorted_centroids")

In [0]:
from pyspark.sql.functions import udf, col
from pyspark.sql.types import IntegerType

def find_increment(cycle_hours, fib_to_centroid):
    if not fib_to_centroid or cycle_hours is None:
        return None
    # Get sorted keys as strings (since Spark map keys are strings)
    fib_keys = sorted(fib_to_centroid.keys(), key=lambda x: int(x))
    # Filter out keys where the centroid value is None
    valid_keys = [k for k in fib_keys if fib_to_centroid[k] is not None]
    if not valid_keys:
        return None
    # Find the closest centroid and its key
    closest_key = min(
        valid_keys,
        key=lambda k: abs(cycle_hours - fib_to_centroid[k])
    )
    # Return the 1-based index (increment) of the closest key
    return fib_keys.index(closest_key) + 1

find_increment_udf = udf(find_increment, IntegerType())

df_with_actual_increment = df_with_sorted_centroids.withColumn(
    "actual_increment",
    find_increment_udf(col("cycle_hours"), col("fib_to_centroid"))
)

display(df_with_actual_increment.select(
    "project", "cycle_hours", "fib_to_centroid", "actual_increment"
))

In [0]:
df_with_actual_increment.write.mode("overwrite").saveAsTable("df_with_actual_increment")

In [0]:
from pyspark.ml.feature import Tokenizer, HashingTF, IDF
from pyspark.ml.functions import vector_to_array
from pyspark.sql.functions import col

tokenizer = Tokenizer(
    inputCol="description",
    outputCol="desc_tokens"
)
df_tokens = tokenizer.transform(df_with_actual_increment)

hashing_tf = HashingTF(
    inputCol="desc_tokens",
    outputCol="desc_tf",
    numFeatures=500
)
df_tf = hashing_tf.transform(df_tokens)

idf = IDF(
    inputCol="desc_tf",
    outputCol="desc_tfidf"
)
idf_model = idf.fit(df_tf)
df_tfidf = idf_model.transform(df_tf)

df_tfidf = df_tfidf.withColumn(
    "desc_tfidf_arr",
    vector_to_array(col("desc_tfidf"))
)

for i in range(500):
    df_tfidf = df_tfidf.withColumn(
        f"desc_dim_{i+1}",
        col("desc_tfidf_arr")[i]
    )

df_tfidf = df_tfidf.drop(
    "desc_tokens",
    "desc_tf",
    "desc_tfidf",
    "desc_tfidf_arr"
)

display(df_tfidf)

In [0]:
num_rows = df_tfidf.count()
num_cols = len(df_tfidf.columns)
print(f"Rows: {num_rows}, Columns: {num_cols}")

In [0]:
df_tfidf.write.mode("overwrite").option("mergeSchema", "true").saveAsTable("df_tfidf")

In [0]:
from pyspark.ml.feature import Tokenizer, HashingTF, IDF
from pyspark.ml.functions import vector_to_array
from pyspark.sql.functions import col

# Tokenize the summary column
tokenizer = Tokenizer(inputCol="summary", outputCol="summary_tokens")
df_tokens = tokenizer.transform(df_tfidf)

# Apply HashingTF to convert tokens into numerical vectors
hashing_tf = HashingTF(inputCol="summary_tokens", outputCol="summary_tf", numFeatures=500)
df_tf = hashing_tf.transform(df_tokens)

# Apply IDF to the HashingTF output
idf = IDF(inputCol="summary_tf", outputCol="summary_tfidf")
idf_model = idf.fit(df_tf)
df_tfidf_with_summary = idf_model.transform(df_tf)

# Convert the TF-IDF vector to an array
df_tfidf_with_summary = df_tfidf_with_summary.withColumn("summary_tfidf_arr", vector_to_array(col("summary_tfidf")))

# Add 200 summary_dim_{i+1} columns
for i in range(500):
    df_tfidf_with_summary = df_tfidf_with_summary.withColumn(f"summary_dim_{i+1}", col("summary_tfidf_arr")[i])

# Drop intermediate columns
df_tfidf_with_summary = df_tfidf_with_summary.drop("summary_tokens", "summary_tf", "summary_tfidf", "summary_tfidf_arr")

display(df_tfidf_with_summary)

In [0]:
df_tfidf_with_summary.write.mode("overwrite").option("mergeSchema", "true").saveAsTable("df_tfidf_with_summary")

In [0]:
df_tfidf_with_summary.write.mode("overwrite").parquet("/mnt/backup/df_tfidf_with_summary_parquet")

In [0]:
df_tfidf_with_summary = spark.table("df_tfidf_with_summary")

In [0]:
from pyspark.sql.functions import col, lit

# List all dimension columns
desc_dim_cols = [f"desc_dim_{i+1}" for i in range(500)]
summary_dim_cols = [f"summary_dim_{i+1}" for i in range(500)]
all_dim_cols = desc_dim_cols + summary_dim_cols

# Ensure all dimension columns exist, fill missing with 0
for dim in all_dim_cols:
    if dim not in df_tfidf_with_summary.columns:
        df_tfidf_with_summary = df_tfidf_with_summary.withColumn(dim, lit(0))

# Compute Spearman correlations
correlations = []
for dim in all_dim_cols:
    corr = df_tfidf_with_summary.stat.corr("actual_increment", dim)
    correlations.append((dim, abs(corr)))

# Get top 100 dimensions by absolute correlation
top_dims = sorted(correlations, key=lambda x: x[1], reverse=True)[:100]
top_dim_names = [dim for dim, _ in top_dims]

# Select required columns
df_top = df_tfidf_with_summary.select(
    ["key", "project", "actual_increment"] + top_dim_names
)

display(df_top)

In [0]:
import pandas as pdimport seaborn as sns

import matplotlib.pyplot as plt

# List all dimension columns with prefixes 'summary_dim_' or 'desc_dim_'
all_dim_cols = [
    col for col in df_tfidf_with_summary.columns
    if col.startswith('summary_dim_') or col.startswith('desc_dim_')
]

# Ensure all dimension columns exist, fill missing with 0
from pyspark.sql.functions import lit
for dim in all_dim_cols:
    if dim not in df_tfidf_with_summary.columns:
        df_tfidf_with_summary = df_tfidf_with_summary.withColumn(dim, lit(0))

# Compute Spearman correlations
correlations = []
for dim in all_dim_cols:
    corr = df_tfidf_with_summary.stat.corr("actual_increment", dim)
    correlations.append((dim, abs(corr)))

# Get top 20 dimensions by absolute correlation
top_dims = sorted(correlations, key=lambda x: x[1], reverse=True)[:20]
top_dim_names = [dim for dim, _ in top_dims]

# Prepare data for heatmap: a single row with correlations
heatmap_df = (
    pd.DataFrame([dict(top_dims)], index=['Correlation'])
    .reindex(columns=top_dim_names)
)

plt.figure(figsize=(20, 2))
sns.heatmap(
    heatmap_df,
    cmap='coolwarm',
    annot=True,
    fmt=".2f",
    linewidths=.5,
    cbar=True
)
plt.title('Correlation Heatmap: Top 50 Dimensions vs actual_increment')
plt.yticks(rotation=0)
plt.show()

In [0]:
import pandas as pd

# Sort and get top 20 correlations
top_20 = sorted(correlations, key=lambda x: x[1], reverse=True)[:20]
top_20_df = pd.DataFrame(top_20, columns=["Dimension", "AbsCorrelation"])

display(top_20_df)

In [0]:
train_df, test_df = df_tfidf_with_summary.randomSplit([0.8, 0.2], seed=42)
display(train_df)
display(test_df)

In [0]:
from pyspark.ml.feature import VectorAssembler

# Select X and Y columns
X_cols = all_dim_cols
Y_col = "actual_increment"

# Drop the existing "features" column if it exists
df_tfidf_with_summary = df_tfidf_with_summary.drop("features")

# Create a VectorAssembler for X
assembler = VectorAssembler(inputCols=X_cols, outputCol="features")
df_assembled = assembler.transform(df_tfidf_with_summary)

# Split the data into training and testing sets
train_df, test_df = df_assembled.randomSplit([0.8, 0.2], seed=42)

In [0]:
# Filter out rows with nulls in label or prediction columns before evaluation
predictions_clean = predictions.filter(
    (predictions[Y_col].isNotNull()) & (predictions["prediction"].isNotNull())
)

# Evaluate the model
evaluator = RegressionEvaluator(
    labelCol=Y_col,
    predictionCol="prediction",
    metricName="r2"
)
r2 = evaluator.evaluate(predictions_clean)

In [0]:
from pyspark.ml.evaluation import RegressionEvaluator

# Evaluate the model using RMSE
evaluator = RegressionEvaluator(labelCol=Y_col, predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions.na.drop())

In [0]:
%pip install azure-ai-textanalytics azure-core

from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.sql.functions import abs as sql_abs, col, when

# Filter out rows with nulls in label or prediction columns
predictions_clean = predictions.filter(
    col(Y_col).isNotNull() & col("prediction").isNotNull()
)

# R^2 calculation
evaluator_r2 = RegressionEvaluator(
    labelCol=Y_col,
    predictionCol="prediction",
    metricName="r2"
)
r2 = evaluator_r2.evaluate(predictions_clean)

# Percent accuracy calculation (for regression, use MAPE as a proxy)
predictions_clean = predictions_clean.withColumn(
    "ape",
    when(
        col(Y_col) != 0,
        sql_abs(col(Y_col) - col("prediction")) / sql_abs(col(Y_col))
    ).otherwise(0)
)
mape = predictions_clean.agg({"ape": "avg"}).collect()[0][0]
percent_accuracy = 1 - mape if mape is not None else None

# Aggregate results as a DataFrame
from pyspark.sql import Row
agg_df = spark.createDataFrame([
    Row(R2=r2, PercentAccuracy=percent_accuracy)
])

display(agg_df)

In [0]:
spark.sql("DROP TABLE IF EXISTS agg_df")
agg_df.write.saveAsTable("agg_df")

In [0]:
agg_df.write.mode("overwrite").parquet("/mnt/backup/agg_df_parquet")

In [0]:
agg_df = spark.table("agg_df")

In [0]:
display(agg_df)

In [0]:
df_with_actual_increment = spark.table("jira_story_point_estimator.default.df_with_actual_increment")

In [0]:
# Repartition the DataFrame into 1000 partitions
df_partitioned = df_with_actual_increment.repartition(1000)

from pyspark.sql.functions import pandas_udf, col
from pyspark.sql.types import ArrayType, FloatType
import pandas as pd

@pandas_udf(ArrayType(FloatType()))
def embed_udf(texts: pd.Series) -> pd.Series:
    from transformers import AutoTokenizer, AutoModel
    import torch

    model_name = "sentence-transformers/all-MiniLM-L6-v2"
    tokenizer = AutoTokenizer.from_pretrained(model_name)
    model = AutoModel.from_pretrained(model_name)
    model.eval()

    embeddings = []
    for text in texts:
        if text is None or text.strip() == "":
            embeddings.append([0.0] * 384)
            continue
        inputs = tokenizer([text], padding=True, truncation=True, return_tensors="pt")
        with torch.no_grad():
            model_output = model(**inputs)
        emb = model_output.last_hidden_state.mean(dim=1)[0].numpy()
        # Use all 384 dimensions
        embeddings.append(emb.tolist())
    return pd.Series(embeddings)

# Apply the embedding UDF on the repartitioned DataFrame
df_embed = (
    df_partitioned
    .withColumn("desc_embed", embed_udf(col("description")))
    .withColumn("summary_embed", embed_udf(col("summary")))
)

# Expand embedding arrays into separate columns (384 dims)
for i in range(384):
    df_embed = df_embed.withColumn(f"desc_dim_{i+1}", col("desc_embed")[i])
    df_embed = df_embed.withColumn(f"summary_dim_{i+1}", col("summary_embed")[i])

df_embed = df_embed.drop("desc_embed", "summary_embed")

display(df_embed)

key project created resolutiondate summary description created_cleaned resolutiondate_cleaned created_unix resolutiondate_unix cycle_hours features cycle_centroids cycle_centroids_rounded sorted_centroids centroids_padded fib_to_centroid actual_increment desc_dim_1 summary_dim_1 desc_dim_2 summary_dim_2 desc_dim_3 summary_dim_3 desc_dim_4 summary_dim_4 desc_dim_5 summary_dim_5 desc_dim_6 summary_dim_6 desc_dim_7 summary_dim_7 desc_dim_8 summary_dim_8 desc_dim_9 summary_dim_9 desc_dim_10 summary_dim_10 desc_dim_11 summary_dim_11 desc_dim_12 summary_dim_12 desc_dim_13 summary_dim_13 desc_dim_14 summary_dim_14 desc_dim_15 summary_dim_15 desc_dim_16 summary_dim_16 desc_dim_17 summary_dim_17 desc_dim_18 summary_dim_18 desc_dim_19 summary_dim_19 desc_dim_20 summary_dim_20 desc_dim_21 summary_dim_21 desc_dim_22 summary_dim_22 desc_dim_23 summary_dim_23 desc_dim_24 summary_dim_24 desc_dim_25 summary_dim_25 desc_dim_26 summary_dim_26 desc_dim_27 summary_dim_27 desc_dim_28 summary_dim_28 desc_dim_29 summary_dim_29 desc_dim_30 summary_dim_30 desc_dim_31 summary_dim_31 desc_dim_32 summary_dim_32 desc_dim_33 summary_dim_33 desc_dim_34 summary_dim_34 desc_dim_35 summary_dim_35 desc_dim_36 summary_dim_36 desc_dim_37 summary_dim_37 desc_dim_38 summary_dim_38 desc_dim_39 summary_dim_39 desc_dim_40 summary_dim_40 desc_dim_41 summary_dim_41 desc_dim_42 summary_dim_42 desc_dim_43 summary_dim_43 desc_dim_44 summary_dim_44 desc_dim_45 summary_dim_45 desc_dim_46 summary_dim_46 desc_dim_47 summary_dim_47 desc_dim_48 summary_dim_48 desc_dim_49 summary_dim_49 desc_dim_50 summary_dim_50 desc_dim_51 summary_dim_51 desc_dim_52 summary_dim_52 desc_dim_53 summary_dim_53 desc_dim_54 summary_dim_54 desc_dim_55 summary_dim_55 desc_dim_56 summary_dim_56 desc_dim_57 summary_dim_57 desc_dim_58 summary_dim_58 desc_dim_59 summary_dim_59 desc_dim_60 summary_dim_60 desc_dim_61 summary_dim_61 desc_dim_62 summary_dim_62 desc_dim_63 summary_dim_63 desc_dim_64 summary_dim_64 desc_dim_65 summary_dim_65 desc_dim_66 summary_dim_66 desc_dim_67 summary_dim_67 desc_dim_68 summary_dim_68 desc_dim_69 summary_dim_69 desc_dim_70 summary_dim_70 desc_dim_71 summary_dim_71 desc_dim_72 summary_dim_72 desc_dim_73 summary_dim_73 desc_dim_74 summary_dim_74 desc_dim_75 summary_dim_75 desc_dim_76 summary_dim_76 desc_dim_77 summary_dim_77 desc_dim_78 summary_dim_78 desc_dim_79 summary_dim_79 desc_dim_80 summary_dim_80 desc_dim_81 summary_dim_81 desc_dim_82 summary_dim_82 desc_dim_83 summary_dim_83 desc_dim_84 summary_dim_84 desc_dim_85 summary_dim_85 desc_dim_86 summary_dim_86 desc_dim_87 summary_dim_87 desc_dim_88 summary_dim_88 desc_dim_89 summary_dim_89 desc_dim_90 summary_dim_90 desc_dim_91 summary_dim_91 desc_dim_92 summary_dim_92 desc_dim_93 summary_dim_93 desc_dim_94 summary_dim_94 desc_dim_95 summary_dim_95 desc_dim_96 summary_dim_96 desc_dim_97 summary_dim_97 desc_dim_98 summary_dim_98 desc_dim_99 summary_dim_99 desc_dim_100 summary_dim_100 desc_dim_101 summary_dim_101 desc_dim_102 summary_dim_102 desc_dim_103 summary_dim_103 desc_dim_104 summary_dim_104 desc_dim_105 summary_dim_105 desc_dim_106 summary_dim_106 desc_dim_107 summary_dim_107 desc_dim_108 summary_dim_108 desc_dim_109 summary_dim_109 desc_dim_110 summary_dim_110 desc_dim_111 summary_dim_111 desc_dim_112 summary_dim_112 desc_dim_113 summary_dim_113 desc_dim_114 summary_dim_114 desc_dim_115 summary_dim_115 desc_dim_116 summary_dim_116 desc_dim_117 summary_dim_117 desc_dim_118 summary_dim_118 desc_dim_119 summary_dim_119 desc_dim_120 summary_dim_120 desc_dim_121 summary_dim_121 desc_dim_122 summary_dim_122 desc_dim_123 summary_dim_123 desc_dim_124 summary_dim_124 desc_dim_125 summary_dim_125 desc_dim_126 summary_dim_126 desc_dim_127 summary_dim_127 desc_dim_128 summary_dim_128 desc_dim_129 summary_dim_129 desc_dim_130 summary_dim_130 desc_dim_131 summary_dim_131 desc_dim_132 summary_dim_132 desc_dim_133 summary_dim_133 desc_dim_134 summary_dim_134 desc_dim_135 summary_dim_135 desc_dim_136 summary_dim_136 desc_dim_137 summ

In [0]:
spark.sql("DROP TABLE IF EXISTS df_embed")
df_embed.write.saveAsTable("df_embed")

In [0]:
import databricks.automl

summary = databricks.automl.regress(
    dataset = spark.table("df_embed"),
    target_col = "actual_increment",
    exclude_cols = ["key", "project", "created", "resolutiondate", "summary", "description"]
)

2025/10/09 05:28:09 INFO databricks.automl.client.manager: AutoML will optimize for R2 metric, which is tracked as val_r2_score in the MLflow experiment.
2025/10/09 05:28:11 INFO databricks.automl.client.manager: MLflow Experiment ID: 1645932984821329
2025/10/09 05:28:11 INFO databricks.automl.client.manager: MLflow Experiment: https://dbc-29a1b711-795e.cloud.databricks.com/?o=317780443222331#mlflow/experiments/1645932984821329
2025/10/09 05:37:54 INFO databricks.automl.client.manager: Data exploration notebook: https://dbc-29a1b711-795e.cloud.databricks.com/?o=317780443222331#notebook/1645932984821334
2025/10/09 07:28:43 INFO databricks.automl.client.manager: AutoML experiment completed successfully.


For exploratory data analysis, open the data exploration notebook 
 To view the best performing model, open the best trial notebook 
 To view details about all trials, navigate to the MLflow experiment 
 Metrics for the best trial: 
 
 <!-- class inlined from webapp/web/js/templates/iframeSandbox.css -->
 
 
 
 
 
 Train 
 Validation 
 Test 
 
 
 
 
 
 r2_score 
 1.000 
 0.998 
 0.998 
 
 

 
 mean_squared_error 
 0.001 
 0.006 
 0.006 
 
 

 
 example_count 
 124436.000 
 41343.000 
 41223.000 
 
 

 
 root_mean_squared_error 
 0.027 
 0.079 
 0.078 
 
 

 
 sum_on_target 
 311096.000 
 103653.000 
 103058.000 
 
 

 
 score 
 1.000 
 0.998 
 0.998 
 
 

 
 mean_absolute_error 
 0.011 
 0.025 
 0.025 
 
 

 
 mean_on_target 
 2.500 
 2.507 
 2.500 
 
 

 
 max_error 
 0.901 
 2.131 
 1.807 
 
 

 
 mean_absolute_percentage_error 
 0.004 
 0.009 
 0.009